***
# **Prak.: <u> P1</u>** $\,\,$ **Semester:** <u>WSxx/yy</u> $\,\,$ **Wochentag:** <u>Mo</u> $\,\,$ **Gruppennr.:** <u>01</u>
***

# **Name:** <u> Fall  </u> $\,\,\,\,$ **Vorname:** <u> Klara </u>
# **Name:** <u> Schal </u> $\,\,\,\,$ **Vorname:** <u> Paul </u>

# **E-Mail Addresse(n):** <u>  someone@somewhere.world </u>

***  

# **Versuch:** <u> Musterprotokoll (P1-0x)</u>
# **Betreuung:** <u> BetreuerIn </u>  $\,\,\,\,$ **Versuchsdurchführung** am <u> 02.01.202x</u>

***
# **1. Abgabe am** <u> 03.01.202x </u>

***
# ggf. **Rückgabe am:** <u> 04.01.202x </u>   $\,\,\,\,$ **Begründung:**
# 
# 
***
# **2. Abgabe am:** <u> 04.01.202x </u>

#=============================================================
# **Erbegnis:** $\,\,$ + / 0 / -   $\,\,\,\,$ **Fehlerrechnung:** Ja / Nein

# **Datum:**  <u> 04.01.1111</u> $\,\,\,\,$ **Handzeichen:** <u>   </u>

***
***

# 
# 

# Musterprotokoll aus VL Computergestützte Datenauswertung
***

## Bestimmung der Erdbeschleunigung 

Eine bekannte Masse $M$ wird an der Feder angebracht und in Schwingung versetzt. 
Aus der Periodendauer der Schwingung wird die Federkonstante $D$ ermitteln.

Mit dieser Information kann aus einer zweiten Messreihe die gesuchte Erdbeschleunigung $g$ bestimmt werden. Dazu werden die Auslenkungen $s$ derselben Feder unter der Last sehr genau bekannter Massen $m_i$ gemessen. Durch die Anpassung des bekannten Zusammenhangs zwischen 
Auslenkung und wirkender Kraft an diese Messdaten wird nun $g$ bestimmt.


*Zusammenstellung der benötigten Formeln:*

Die Schwingungsfrequenz $f= \omega/(2\pi)$ der Schwingung einer Masse
an einer Feder mit der Federkonstanten $D$ ist gegeben über

\begin{equation} 
  \omega = \sqrt{\frac {D}{m_\mathrm{eff}}} \,. 
\end{equation} 

$m_\mathrm{eff}$ ist dabei die effektive bewegte Masse, die sich aus der
angehängten Masse $M$ und der Federmasse $M_\mathrm{F}$ ergibt:

\begin{equation}
  m_\mathrm{eff} = M + \frac{1}{3} M_\mathrm{F} \,. 
\end{equation}

Der Zusammenhang zwischen der auf das Ende der
Feder wirkenden Kraft $F$ und der Auslenkung $s$ der Feder
ist gegeben durch

\begin{equation}
  F =  D \, s \, . 
\end{equation}

Wenn die Kraft durch die Schwerkraft einer angehängten Masse
$m$ erzeugt wird, gilt also

\begin{equation} \label{equ_Hooke} 
  s = \frac {g \, m } {D} \, . 
\end{equation} 

  


#### Allgemeine Einstellungen und Pakete

In [ ]:
from __future__ import division, print_function
#
import sys, os
#
import numpy as np, matplotlib.pyplot as plt
import PhyPraKit as ppk

%matplotlib inline

# the following line provides larger figure 
# plt.rcParams['figure.dpi'] = 100 # default 75


#### Aufgabe A: Bestimmung der Frequenz der Schwingung aus den Daten in der Datei _HandyPendel.csv_
 
 Diese Daten wurden durch
Auslesen des Beschleunigungssensors eines Mobiltelefons mit der 
App *phyphox* gewonnen. Das Handy mit der Masse $M={141.74}\,$g 
wurde dazu an der Feder mit der Masse $M_\mathrm{F}={15.40}\,$g befestigt
und in vertikale Schwingungen versetzt. 

Eine sehr genaue Bestimmung der Frequenz gelingt durch eine 
Autokorrelationsanalyse der Schwingungsdaten. Dazu können Sie 
sich am Beispiel 
   *test_AutoCorrelation.py* aus der fünften Vorlesung 
orientieren. Die Unsicherheit der Frequenzbestimmung erhalten Sie am
einfachsten wie im Beispiel aus der Streuung der 
Abstände zwischen den Maxima bzw. Minima der Autokorrelationsfunktion.
Die Messungen der Massen wurden mit einer sehr präzisen Waage
mit einer Genauigkeit von $\pm{0.1}$g durchgeführt. 

Bestimmen Sie die Federkonstante $D$ und deren Unsicherheit.
Wenden Sie dazu das einfache Fehlerfortpflanzungsgesetz an und
propagieren Sie damit die Unsicherheit der Frequenz- und 
Massenmessungen auf die Unsicherheit von $D$.
  

** Einlesen der mit der *phyphox* App generierten Daten  

In [ ]:
''' Einlesen und Analyse von Daten aus der Android App "Physics Toolbox
  .. author:: Guenter Quast <g.quast@kit.edu>
'''

# Einlesen der Sensor-Daten im CSV-Format
# -----------------------------------------
if len(sys.argv) == 2:
    infile = sys.argv[1]
else:
    infile = 'HandyPendel.csv'
print('*==* script', sys.argv[0], 'reading from file', infile)

# open file for read
h, data = ppk.readCSV(infile, 1)
t = data[0]
a = data[2]  # vertikale Beschleunigung
# a=data[4] # Gesamtbeschleunigung

# t, a = np.loadtxt(infile, delimiter=',', unpack=True)
print(len(t), 'Datenpunkte eingelesen')


**Autokorrelations-Analyse**

In [ ]:
# Autokorrelations-Analyse
# -----------------------------------------
print("** Autokorrelations-Analyse:")
ac_a = ppk.autocorrelate(a)
ac_t = t

# Suche nach Maxima und Minima in der Autokorrelationsfunktion
ac_width = 30
pidxac = ppk.convolutionPeakfinder(ac_a, ac_width, th=0.6)   # Peaks
didxac = ppk.convolutionPeakfinder(-ac_a, ac_width, th=0.6)  # Dips
if len(pidxac) > 1:
    print(" --> %i auto-correlation peaks found" % (len(pidxac)))
    pidxac[0] = 0  # first peak is at 0 by construction
    ac_tp, ac_ap = np.array(ac_t[pidxac]), np.array(ac_a[pidxac])
    ac_td, ac_ad = np.array(ac_t[didxac]), np.array(ac_a[didxac])
else:
    print("*!!* not enough correlation peaks found")
    sys.exit()

# Generate Plots
# -----------------------------------------
units = ['s', r'$\mathrm{m/s^2}$']
fig1 = plt.figure(1, figsize=(7.5, 12.))
fig1.subplots_adjust(left=0.14, bottom=0.1, right=0.97, top=0.93,
                     wspace=None, hspace=.25)

# Plot1: Beschleunigung vs. Zeit
ax1 = fig1.add_subplot(3, 1, 1)
ax1.plot(t, a)
ax1.set_xlabel('Zeit ' + units[0], size='large')
ax1.set_ylabel('Beschleunigung ' + units[1], size='large')
ax1.grid()

# Plot2: Autokorrelation vs. Zeit
ax2 = fig1.add_subplot(3, 1, 2)
ax2.plot(ac_tp, ac_ap, 'rx', alpha=0.9, label='large peaks')
ax2.plot(ac_td, ac_ad, 'gx', alpha=0.9, label='large dips')
ax2.plot(ac_t, ac_a)
ax2.set_xlabel('Zeit ' + units[0], size='large')
ax2.set_ylabel('Autokorrelation', size='large')
ax2.grid()

# Plot3: Histogramm Peaks/Dips vs. Zeitdifferenz
dtp = ac_tp[1:]-ac_tp[:-1]
dtd = ac_td[1:]-ac_td[:-1]

ax3 = fig1.add_subplot(3, 1, 3)
bins = np.linspace(min(min(dtp), min(dtd)), max(max(dtp), max(dtd)), 50)
bc, be, _ = ax3.hist([dtp, dtd], bins, stacked=True,
                     color=['r', 'g'], label=['peaks', 'dips'], alpha=0.5)
ax3.set_xlabel('Zeitdifferenz der peaks / dips (ms)', size='large')
ax3.legend(loc='best', numpoints=1, prop={'size': 10})
ax3.set_ylabel('Häufigkeit', size='large')
# Bei matplotlib >= 2.2.0 funktioniert auch
# ax3.set_ylabel('Häufigkeit', size='large')
ax3.grid()

print("** Histogram-Statistik:")
m_dtp, s_dtp, sm_dtp = ppk.histstat(bc[0], be, pr=False)
m_dtd, s_dtd, sm_dtd = ppk.histstat(bc[1], be, pr=False)
print(" --> mean time difference of peaks: (%.4g +/- %.2g) ms"
      % (m_dtp, sm_dtp))
print("                             dips:  (%.4g +/- %.2g) ms"
      % (m_dtd, sm_dtd))
ax3.text(0.1, 0.75,  "peaks: (%.4g$\pm$%.2g) ms" % (m_dtp, sm_dtp),
         transform=ax3.transAxes)
ax3.text(0.1, 0.65, " dips:  (%.4g$\pm$%.2g) ms" % (m_dtd, sm_dtd),
         transform=ax3.transAxes)

plt.show()



####  Berechnung der Federkonstanten


In [ ]:
# Berechnung der Federkonstanten (incl. Unsicherheiten)
# ---------------------------------------------------------
print("** Berechnung der Zielgroessen:")
wp = (1/sm_dtp)**2
wd = (1/sm_dtd)**2
T = 1./(wp+wd) * (wp * m_dtp + wd * m_dtd)  # gemittelte Periodendauer
sT = np.sqrt(1./(wp + wd))  # Unsicherheit
Nu = 1/T                    # Frequenz
sNu = sT/T * Nu
print(" -> Periode =  %.5g +/- %.2g" % (T, sT))
print(" -> Frequenz = %.5g +/- %.2g" % (Nu, sNu))

# Pendel- und Federmassen in g
MHandy = 141.71
MFeder = 15.40
sM = 0.1
Meff = MHandy + 1./3. * MFeder
D = (2.*np.pi*Nu)**2 * Meff/1000.
sD = np.sqrt((2.*sNu/Nu)**2 + (sM/Meff)**2) * D
print("->> Federkonstante D = %.5g +/- %.2g" % (D, sD))


### Aufgabe B: Anpassung Hooke'sches Gesetz

Führen Sie mit _kafe_ eine Anpassung  analog zum Beispiel
*fit_example.py* aus der sechsten Vorlesung durch. 

Sie können dazu den Zusammenhang $s(g)$  direkt als Fit-Funktion
implementieren. Bestimmen Sie so die Erdbeschleunigung $g$ und deren
Unsicherheit. 

Begründen Sie, warum für die Unsicherheit auf das 
Ergebnis für $g$ die Unsicherheiten der Federkonstanten 
$D$ aus Aufgabenteil **A** und die Unsicherheiten der 
Massenmessungen $\Delta m_i$ vernachlässigt werden können. 

In [ ]:
# import kafe2 and set options
from kafe2 import XYContainer, XYFit, Plot
# set better default figure size for kafe2
#plt.rcParams['figure.figsize']=[12., 5.] 
#        !!!  must be done after importing kafe2 (will else be overriden)


In [ ]:
# Anpassung Hooke'sches Gesetz
# -----------------------------------------
print("** Anpassung des Hooke'schen Gesetzes")


# Fit-Funktion für Funktionsanpassung des Hooke'schen Gesetzes
# ---- fit function definition in kafe style
#         (decorators for nice output not mandatory)

def Hooke(m, g=10., D=10.):
    s = m * g / D
    return s

# set the function
fitf = Hooke             # own definition

# Einlesen der Messreihe
m, s = np.loadtxt("Messtabelle.txt", unpack=True)
print("  eingelesene Messreihe:")
print("    Massenwerte (g): ", m)
print("    Auslenkungen (m):", s)
print()
mm = m/1000.   # in kg statt g
ms = s/100.    # in m statt cm
me = 0.1/1000.  # Unsicherheit Massenmessung
se = 0.2/100.   # Unsicherheit Auslenkung

# Perform Fit
# - option 1: use one of the suitable Phyprakit interfaces

#    - select   k2Fit() or mFit() (only these can handle parameter constraints)
#thisFit = ppk.k2Fit
thisFit = ppk.xyFit
FitResult = thisFit(Hooke, mm, ms, me, se, 
                    constraints= ['D', D, sD],
                    data_legend = 'Daten aus Tabelle',
                    axis_labels=['Masse m (kg)', 'Auslenkung s (m)'],
     #           model_name=(r'\frac{{m \cdot g }}{{D}}'),
                    model_legend = "Hooke'sches Gesetz",
                    quiet=True,                     
                    plot = True)

if thisFit is ppk.xyFit:      # xyFit() returns confidence regions, symmetrize
    parv, paru, cor, chi2, parn = FitResult.values()
else:
    parv, paru, cor, chi2 = FitResult
    
# - option2: using kafe2 directly  (remove """ """ to enable)
"""
kdata = XYContainer(mm, ms)
kdata.add_error('x', me)
kdata.add_error('y', se)
kdata.label = 'Daten aus Tabelle'
kdata.axis_labels = ['Masse m (kg)', 'Auslenkung s (m)']

kfit = XYFit(kdata, fitf)    # create the fit
kfit.assign_model_function_latex_expression(r'\frac{{m \cdot g }}{{D}}')
kfit.add_parameter_constraint('D', D, sD)
kfit.do_fit()                   # perform fit

kplot = Plot(kfit)         # create plot object
# einige Grafik-Optionen:
kplot.customize('data', 'markersize', [5])
kplot.customize('data', 'color', ['darkblue'])
kplot.customize('model_line', 'label', ["Hooke'sches Gesetz"])
kplot.customize('model_error_band', 'label', [r'$\pm 1 \sigma$'])
kplot.customize('model_line', 'color', ['darkred'])
kplot.customize('model_line', 'linestyle', ['--'])
# eventually overwrite/set names for Data set, x-label and y-label
kplot.customize('data', 'label', ['Daten aus Tabelle'])
kplot.plot()           # make plots

parv = kfit.parameter_values 
paru = kfit.parameter_errors

"""

# show plot and print final result
print('\n  Ergebnis:    Erdbeschleunigung g = %.3f [%.3f, +%.3f] '%(parv[0], paru[0,0], paru[0,1]) )

# Diskussion des Ergebnisses

Lorem ipsum dolor sit amet, consetetur sadipscing elitr, sed diam nonumy eirmod tempor invidunt ut labore et dolore magna aliquyam erat, sed diam voluptua. At vero eos et accusam et justo duo dolores et ea rebum. Stet clita kasd gubergren, no sea takimata sanctus est Lorem ipsum dolor sit amet. Lorem ipsum dolor sit amet, consetetur sadipscing elitr, sed diam nonumy eirmod tempor invidunt ut labore et dolore magna aliquyam erat, sed diam voluptua. At vero eos et accusam et justo duo dolores et ea rebum. Stet clita kasd gubergren, no sea takimata sanctus est Lorem ipsum dolor sit amet.